In [292]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import json

In [335]:
station_id = "8443970"
threshold = "1yr"
units = "ft"

In [336]:
fname = "../data/day_min_max/" + station_id + ".pickle"
dy = pd.read_pickle(fname)

blank = dy["max"].isna() | dy["min"].isna()
dy.loc[blank, :] = None

dy = (dy * 3.28084).round(3) if units == "ft" else dy

dy

max     min
time                     
1921-01-01    NaN     NaN
1921-01-02    NaN     NaN
1921-01-03    NaN     NaN
1921-01-04    NaN     NaN
1921-01-05    NaN     NaN
...           ...     ...
2021-03-28  1.007 -10.541
2021-03-29  1.588 -12.339
2021-03-30  0.689 -12.339
2021-03-31  0.955 -11.988
2021-04-01  0.256  -9.426

[36616 rows x 2 columns]

In [337]:
dy = dy.dropna()
tdiff = dy.index[1:] - dy.index[:-1]
splits = np.hstack([[0], np.where(tdiff.days.values > 1)[0] + 1, -1])
splits

array([    0,    30,  8599,  8604, 14571, 17213, 17475, 18234, 19309,
       19315, 19785, 20426, 29956, 29958, 31990, 34853,    -1])

In [338]:
dy_splits = [dy.iloc[i1:i2] for i1, i2 in zip(splits[:-1], splits[1:])]
dy_splits

[              max     min
 time                     
 1921-05-03 -1.696  -9.298
 1921-05-04 -1.296  -9.396
 1921-05-05 -0.699  -9.498
 1921-05-06 -0.098  -9.698
 1921-05-07  0.404 -10.299
 1921-05-08  0.702 -10.699
 1921-05-09  0.804 -11.398
 1921-05-10  1.102 -10.597
 1921-05-11  0.804 -10.299
 1921-05-12  0.102 -10.499
 1921-05-13 -0.098 -10.699
 1921-05-14 -0.299 -10.997
 1921-05-15 -0.699 -10.699
 1921-05-16 -0.896 -10.699
 1921-05-17 -0.797 -10.699
 1921-05-18 -0.597 -10.597
 1921-05-19 -0.499 -10.699
 1921-05-20 -0.499 -11.798
 1921-05-21 -0.299 -11.995
 1921-05-22 -0.299 -10.499
 1921-05-23 -0.397 -10.699
 1921-05-24 -0.397 -10.699
 1921-05-25 -1.198 -10.699
 1921-05-26 -0.597 -10.098
 1921-05-27 -1.096 -10.098
 1921-05-28 -1.598  -9.898
 1921-05-29 -1.696  -9.298
 1921-05-30 -1.798  -9.596
 1921-05-31 -1.998  -9.396
 1921-06-01 -1.998  -9.298,
               max     min
 time                     
 1921-07-24 -1.198 -10.295
 1921-07-25 -1.496 -10.197
 1921-07-26 -1.594  -9.895


In [339]:
fname = "../data/levels/" + station_id + ".json"
with open(fname, "r") as f:
    levels = json.load(f)

if units == "ft":
    for lev_type in ["datums", "flood", "extremes"]:
        levels[lev_type] = {
            h: np.round(levels[lev_type][h] * 3.28084, 3) for h in levels[lev_type]
        }
    for n in range(len(levels["topten"])):
        levels["topten"][n]["height"] = np.round(
            levels["topten"][n]["height"] * 3.28084, 3
        )

levels


{'datums': {'msl': -5.069, 'mllw': -10.272, 'mhhw': 0.0, 'gt': 10.272},
 'flood': {'minor': 2.051, 'moderate': 2.933, 'major': 4.249},
 'extremes': {'100yr': 4.61, '10yr': 3.514, '2yr': 2.667, '1yr': 1.847},
 'topten': [{'date': '2018-01-04', 'height': 4.892},
  {'date': '1978-02-07', 'height': 4.823},
  {'date': '2018-03-02', 'height': 4.357},
  {'date': '1987-01-02', 'height': 3.924},
  {'date': '1991-10-30', 'height': 3.865},
  {'date': '1979-01-28', 'height': 3.763},
  {'date': '1992-12-12', 'height': 3.753},
  {'date': '1959-12-29', 'height': 3.704},
  {'date': '1972-02-19', 'height': 3.615},
  {'date': '2014-01-03', 'height': 3.563}]}

In [340]:
thresholds = {
    **levels["flood"],
    **levels["extremes"],
    **{d: levels["datums"][d] for d in levels["datums"] if d in ["msl", "mhhw"]},
}
thresholds


{'minor': 2.051,
 'moderate': 2.933,
 'major': 4.249,
 '100yr': 4.61,
 '10yr': 3.514,
 '2yr': 2.667,
 '1yr': 1.847,
 'msl': -5.069,
 'mhhw': 0.0}

In [341]:
threshold_names = {
    "minor": "NOAA/NOS minor",
    "moderate": "NOAA/NOS moderate",
    "major": "NOAA/NOS major",
    "100yr": "100-year flood",
    "10yr": "10-year flood",
    "2yr": "2-year flood",
    "1yr": "1-year flood",
    "msl": "Mean sea level",
    "mhhw": "Mean higher high water",
}
# threshold_names = {
#     h: threshold_names[h] + " (" + str(thresholds[h]) + " " + units + ")"
#     for h in threshold_names
# }
threshold_names


{'minor': 'NOAA/NOS minor',
 'moderate': 'NOAA/NOS moderate',
 'major': 'NOAA/NOS major',
 '100yr': '100-year flood',
 '10yr': '10-year flood',
 '2yr': '2-year flood',
 '1yr': '1-year flood',
 'msl': 'Mean sea level',
 'mhhw': 'Mean higher high water'}

In [342]:
fname = "../data/htf_observed/" + station_id + ".json"
with open(fname, "r") as f:
    htfo = json.load(f)
htfo

{'annual': {'years': [1922,
   1923,
   1924,
   1925,
   1926,
   1927,
   1928,
   1929,
   1930,
   1931,
   1932,
   1933,
   1934,
   1935,
   1936,
   1937,
   1938,
   1939,
   1940,
   1941,
   1942,
   1943,
   1944,
   1945,
   1946,
   1947,
   1948,
   1949,
   1950,
   1951,
   1952,
   1953,
   1954,
   1955,
   1956,
   1957,
   1958,
   1959,
   1960,
   1961,
   1962,
   1963,
   1964,
   1965,
   1966,
   1967,
   1968,
   1969,
   1970,
   1971,
   1972,
   1973,
   1974,
   1975,
   1976,
   1977,
   1978,
   1979,
   1980,
   1981,
   1982,
   1983,
   1984,
   1985,
   1986,
   1987,
   1988,
   1989,
   1990,
   1991,
   1992,
   1993,
   1994,
   1995,
   1996,
   1997,
   1998,
   1999,
   2000,
   2001,
   2002,
   2003,
   2004,
   2005,
   2006,
   2007,
   2008,
   2009,
   2010,
   2011,
   2012,
   2013,
   2014,
   2015,
   2016,
   2017,
   2018,
   2019,
   2020,
   2021],
  'levels': {'minor': [0,
    0,
    0,
    0,
    1,
    0,
    0,
    0,
    0

In [347]:
def fill_color(hex, opacity):
    hex = hex.lstrip("#")
    hlen = len(hex)
    return "rgba" + str(
        tuple(
            [int(hex[i : i + hlen // 3], 16) for i in range(0, hlen, hlen // 3)]
            + [opacity]
        )
    )

col = [
    "#0072B2",
    "#56B4E9",
    "#CC79A7",
    "#009E73",
    "#F0E442",
    "#D55E00",
    "#E69F00",
]

fcol = [fill_color(c, 0.25) for c in col if c[0] == "#"]

In [359]:
black = "#222222"
gray = "#aaaaaa"

fig = go.Figure()
fig = make_subplots(
    rows=2,
    cols=1,
    row_heights=[0.75, 0.25],
    shared_xaxes=True,
    vertical_spacing=0.12,
)

traces = []
made_flood_leg_already = False
for n, dy in enumerate(dy_splits):
    floods = dy["max"].loc[dy["max"] > thresholds[threshold]]
    if (floods.count() > 0) and not made_flood_leg_already:
        flood_leg = True
        made_flood_leg_already = True
    traces.extend(
        [
            {
                "x": dy.index.values,
                "y": dy["min"].values,
                "type": "scatter",
                "fill": "tozeroy",
                "fillcolor": "rgba(1, 1, 1, 0)",
                "showlegend": False,
                "mode": "lines",
                "line": {"color": col[0], "width": 0},
                "hoverinfo": "none",
            },
            {
                "x": dy.index.values,
                "y": dy["max"].values,
                "type": "scatter",
                "fill": "tonexty",
                "fillcolor": col[1],
                "showlegend": True if n == 0 else False,
                "name": "Observed daily range (min to max)",
                "mode": "none",
                "hoverinfo": "none",
                "legendgroup": "1",
            },
            {
                "x": floods.index.values,
                "y": floods.values,
                "type": "scatter",
                "showlegend": flood_leg,
                "name": "Flooding days (daily max exceeds "
                + threshold_names[threshold]
                + ")",
                "mode": "markers",
                "marker": {"color": col[5]},
                "customdata": floods.index.strftime("%Y-%m-%d").to_list(),
                "hovertemplate": "%{y} " + units + "<extra>%{customdata}</extra>",
                "legendgroup": "1",
            },
        ]
    )
    flood_leg = False

for trc in traces:
    fig.add_trace(trc, row=1, col=1)

thrsh_labels = []
thrsh_levels = []
thrsh_traces = []
for thrsh in thresholds:
    color = black if thrsh == threshold else gray
    lw = 2 if thrsh == threshold else 0
    fig.add_hline(
        y=thresholds[thrsh],
        line={"color": color, "width": lw},
        layer="below",
        row=1,
        col=1,
    )
    static_labels = [threshold, "msl", "mhhw"]
    if thrsh in static_labels:
        thrsh_labels.append(
            {
                "x": 1.004,
                "y": thresholds[thrsh],
                "text": "<b>"
                + threshold_names[thrsh]
                + "("
                + str(thresholds[thrsh])
                + " "
                + units
                + ")</b>"
                if thrsh == threshold
                else threshold_names[thrsh]
                + "("
                + str(thresholds[thrsh])
                + " "
                + units
                + ")",
                "font": {"color": black if thrsh == threshold else gray},
                "xref": "paper",
                "yref": "y1",
                "xanchor": "left",
                "yanchor": "middle",
                "borderpad": 2,
                "showarrow": False,
            }
        )
    thrsh_levels.append(thresholds[thrsh])
    fig.add_trace(
        {
            "x": [1],
            "y": [thresholds[thrsh]],
            "xaxis": "x3",
            "type": "scatter",
            "showlegend": False,
            "mode": "markers",
            "marker": {
                "symbol": "arrow-left",
                "color": black if thrsh == threshold else gray,
                "size": 10,
            },
            "hovertemplate": "none"
            if thrsh in static_labels
            else "%{y} " + units + "<extra>" + threshold_names[thrsh] + "</extra>",
        },
    )

fig.update_layout(annotations=thrsh_labels)

units_full = "feet" if units == "ft" else "meters"
fig.update_yaxes(
    title_text=units_full + " above MHHW",
    side="right",
    range=[
        1.25 * levels["datums"]["mllw"],
        max(
            [
                1.05 * thresholds[threshold],
                1.15 * dy["max"].max(),
                1.05 * thresholds["moderate"],
            ]
        ),
    ],
    row=1,
    col=1,
)

htfo_time = [pd.Timestamp(str(y - 1) + "-11-01") for y in htfo["annual"]["years"]]
traces = [
    {
        "x": htfo_time,
        "y": [c if c >= 0 else None for c in htfo["annual"]["levels"][threshold]],
        "type": "bar",
        "marker": {"color": col[0]},
        "name": "Annual counts of flooding days",
        "customdata": [
            "05/" + str(d.year) + "–04/" + str(d.year + 1) for d in htfo_time
        ],
        "hovertemplate": "%{y} days <extra>%{customdata}</extra>",
        "legendgroup": "2",
    },
]

for trc in traces:
    fig.add_trace(
        trc,
        row=2,
        col=1,
    )

fig.update_yaxes(
    title_text="days",
    side="right",
    range=[-1, max(htfo["annual"]["levels"][threshold]) + 1],
    row=2,
    col=1,
)

time_lims = [
    str(max([1990, dy_splits[0]["max"].index.year[0]])),
    str(dy["max"].index.year[-1] + 1),
]
fig.update_xaxes(range=time_lims)

fig.update_layout(
    template="none",
    height=600,
    margin=dict(l=70, r=250, b=30, t=20, pad=0),
    font=dict(size=14),
    xaxis=dict(
        layer="below traces",
        zeroline=False,
        matches="x2",
    ),
    xaxis3=dict(
        layer="below traces",
        zeroline=False,
        overlaying="x",
        range=[0, 1.013],
        fixedrange=True,
        visible=False,
    ),
    yaxis=dict(
        layer="below traces",
        side="left",
        zeroline=False,
    ),
    yaxis2=dict(
        layer="below traces",
        side="left",
        fixedrange=True,
    ),
    legend=dict(
        x=0.02,
        y=0.33,
        bgcolor="rgba(0, 0, 0, 0)",
        # traceorder="reversed",
        itemclick=False,
        itemdoubleclick=False,
        orientation="h",
    ),
    modebar=dict(
        remove=["toImage", "lasso", "select", "zoomIn", "zoomOut"],
        orientation="h",
        color="#333333",
        bgcolor=None,
    ),
)

fig


In [360]:
thresholds

{'minor': 2.051,
 'moderate': 2.933,
 'major': 4.249,
 '100yr': 4.61,
 '10yr': 3.514,
 '2yr': 2.667,
 '1yr': 1.847,
 'msl': -5.069,
 'mhhw': 0.0}

In [366]:
[*[thrsh for thrsh in thresholds if thrsh != threshold], *[threshold]]

['minor', 'moderate', 'major', '100yr', '10yr', '2yr', 'msl', 'mhhw', '1yr']